In [2]:
import pandas as pd

# Load your data
pma = pd.read_csv('D:\MS\Summer-25\Spark\Population Estimates\csv_pma\psam_p25.csv')
hma = pd.read_csv('D:\MS\Summer-25\Spark\Population Estimates\csv_hma\psam_h25.csv')

merged_ma = pd.merge(pma, hma, on="SERIALNO")
print(f"Merged dataset shape: {merged_ma.shape}")

def derive_mom_loc_head(df):
    """
    Fixed version that uses the input dataframe parameter correctly
    """
    # Create a copy to avoid modifying original data
    result_df = df.copy()  # Use df parameter, not hardcoded merged_ma
    
    # Initialize MOM_LOC_HEAD column
    result_df['MOM_LOC_HEAD'] = None
    
    # Group by household (SERIALNO)
    for serialno, household in df.groupby('SERIALNO'):
        
        # Step 1: Find head of household (RELSHIPP == 20)
        head_records = household[household['RELSHIPP'] == 20]
        
        if len(head_records) == 0:
            # No head of household found, skip this household
            continue
        
        # Take first head if multiple (shouldn't happen in clean data)
        head = head_records.iloc[0]
        head_age = head['AGEP']
        head_sporder = head['SPORDER']
        
        # Step 3: Find mother candidates in same household
        candidates = household[
            (household['SEX'] == 2) &  # Female
            (household['AGEP'] <= head_age - 12)  # At least 12 years older than head
        ]
        
        if len(candidates) == 0:
            # No candidates found
            mom_sporder = None
        else:
            # Step 4: Prioritize RELSHIPP == 29 (mother)
            mother_candidates = candidates[candidates['RELSHIPP'] == 29]
            
            if len(mother_candidates) > 0:
                # Found mother relationship, take first one
                mom_sporder = mother_candidates.iloc[0]['SPORDER']
            else:
                # No mother relationship found, take first candidate that fits age/sex criteria
                mom_sporder = candidates.iloc[0]['SPORDER']
        
        # Assign MOM_LOC_HEAD to the head of household record
        head_mask = (result_df['SERIALNO'] == serialno) & (result_df['SPORDER'] == head_sporder)
        result_df.loc[head_mask, 'MOM_LOC_HEAD'] = mom_sporder
    
    return result_df

# Run the function on your merged dataset
print("Processing MOM_LOC_HEAD...")
result_data = derive_mom_loc_head(merged_ma)

# Check the results
print(f"Final dataset shape: {result_data.shape}")
print("\nSample of results (heads of household only):")
heads_sample = result_data[result_data['RELSHIPP'] == 20][['SERIALNO', 'SPORDER', 'AGEP', 'SEX', 'RELSHIPP', 'MOM_LOC_HEAD']].head(10)
print(heads_sample)

# Summary statistics
print(f"\nSummary:")
total_heads = len(result_data[result_data['RELSHIPP'] == 20])
heads_with_mom = len(result_data[(result_data['RELSHIPP'] == 20) & (result_data['MOM_LOC_HEAD'].notna())])
print(f"Total heads of household: {total_heads}")
print(f"Heads with identified mothers: {heads_with_mom}")
print(f"Percentage with mothers identified: {heads_with_mom/total_heads*100:.1f}%")



heads_with_mothers = result_data[
    (result_data['RELSHIPP'] == 20) & 
    (result_data['MOM_LOC_HEAD'].notna())
]

print(f"\nFound {len(heads_with_mothers)} heads of household with identified mothers")
print(heads_with_mothers)

Merged dataset shape: (73126, 527)
Processing MOM_LOC_HEAD...
Final dataset shape: (73126, 528)

Sample of results (heads of household only):
           SERIALNO  SPORDER  AGEP  SEX  RELSHIPP MOM_LOC_HEAD
5140  2023HU0000043        1    47    2        20         None
5141  2023HU0000074        1    88    2        20         None
5142  2023HU0000076        1    59    1        20         None
5143  2023HU0000090        1    64    2        20         None
5144  2023HU0000123        1    54    1        20         None
5145  2023HU0000128        1    28    1        20         None
5146  2023HU0000140        1    31    2        20         None
5148  2023HU0000167        1    53    1        20         None
5152  2023HU0000189        1    80    2        20         None
5155  2023HU0000535        1    24    1        20         None

Summary:
Total heads of household: 28911
Heads with identified mothers: 6853
Percentage with mothers identified: 23.7%

Found 6853 heads of household with identifie

In [4]:
ipums_df = pd.read_csv(r'D:\MS\Summer-25\Spark\Population Estimates\usa_00214.csv')
# ipums_res_merge = pd.concat([ipums_df, result_data])
# print(ipums_res_merge['MOM_LOC_HEAD'].equals(ipums_res_merge['MOMLOC_HEAD']))
import numpy as np


In [5]:
# ipums_res_merge[['CBSERIAL', 'SERIALNO']]
# ipums_df[['CBSERIAL', 'SERIAL']]
ipums_df['CBSERIAL_NEW'] = (
    ipums_df['CBSERIAL'].astype(str).str[:4] + 'HU' + 
    ipums_df['CBSERIAL'].astype(str).str[6:]
)

FLAG_TO_DIGITS = {'HU': '00',
                  'GQ': '00'}          # <- extend if needed
ser = result_data['SERIALNO'].astype(str)            # make sure it is string
result_data['SERIALNO_NEW'] = (
    ser.str[:4]                                   # YYYY
    + ser.str[4:6].map(FLAG_TO_DIGITS).fillna('99')   # flag → digits
    + ser.str[6:]                                 # remaining 7 digits
).astype(np.int64)    
# ipums_res_merge = pd.concat([ipums_df, result_data])
# ipums_res_merge[['CBSERIAL_NEW']]
# ipums_df[['CBSERIAL_NEW']]
# for i in ipums_df['CBSERIAL'].unique():
#     print(i)
result_data[['SERIALNO_NEW']]

SERIALNO_NEW
0      2023000000077
1      2023000000098
2      2023000000109
3      2023000000114
4      2023000000135
...              ...
73121  2023001459883
73122  2023001459883
73123  2023001459883
73124  2023001459891
73125  2023001459906

[73126 rows x 1 columns]

In [43]:
ipums_res_concat = pd.concat([ipums_df, result_data[['SERIALNO_NEW', 'MOM_LOC_HEAD']]])
ipums_res_concat[['CBSERIAL', 'SERIALNO_NEW', 'MOM_LOC_HEAD', 'MOMLOC_HEAD', 'STATEFIP']].to_csv('ipums_res_concat.csv', index=False)



In [7]:
file_path = r'D:\MS\Summer-25\Spark\Population Estimates\csv_pma\usa_00001_temp.dat'

colspecs = [
    (0,   4),   # YEAR        1-4
    (4,  10),   # SAMPLE      5-10
    (10, 18),   # SERIAL      11-18
    (18, 31),   # CBSERIAL    19-31
    (31, 41),   # HHWT        32-41   (2 implied decimals)
    (41, 54),   # CLUSTER     42-54
    (54, 56),   # STATEICP    55-56
    (56, 58),   # STATEFIP    57-58
    (58, 70),   # STRATA      59-70
    (70, 71),   # GQ          71-71
    (71, 75),   # PERNUM      72-75
    (75, 77),   # CBPERNUM    76-77
    (77, 87),   # PERWT       78-87   (2 implied decimals)
    (87, 89),   # MOMLOC      88-89
    (89, 91),   # POPLOC      90-91
    (91, 93),   # RELATE      92-93
    (93, 97),   # RELATED     94-97
    (97, 98),   # SEX         98-98
    (98,101)    # AGE         99-101
]

names = [
    'YEAR', 'SAMPLE', 'SERIAL', 'CBSERIAL', 'HHWT', 'CLUSTER',
    'STATEICP', 'STATEFIP', 'STRATA', 'GQ', 'PERNUM', 'CBPERNUM',
    'PERWT', 'MOMLOC', 'POPLOC', 'RELATE', 'RELATED', 'SEX', 'AGE'
]

df = pd.read_fwf(file_path, colspecs=colspecs, names=names)

df.head(10)

YEAR  SAMPLE  SERIAL       CBSERIAL  HHWT        CLUSTER  STATEICP  \
0  2023  202301       1  2023010000113   600  2023000000011        41   
1  2023  202301       2  2023010000180  2700  2023000000021        41   
2  2023  202301       3  2023010000181  4700  2023000000031        41   
3  2023  202301       4  2023010000250  1100  2023000000041        41   
4  2023  202301       5  2023010000340  5700  2023000000051        41   
5  2023  202301       6  2023010000364  5200  2023000000061        41   
6  2023  202301       7  2023010000493  4300  2023000000071        41   
7  2023  202301       8  2023010000537   100  2023000000081        41   
8  2023  202301       9  2023010000558   300  2023000000091        41   
9  2023  202301      10  2023010000796  4100  2023000000101        41   

   STATEFIP  STRATA  GQ  PERNUM  CBPERNUM  PERWT  MOMLOC  POPLOC  RELATE  \
0         1  280201   3       1         1    600       0       0      13   
1         1   10001   3       1         1   2700       0       0      13   
2         1   40201   4       1         1   4700       0       0      12   
3         1  270201   3       1         1   1100       0       0      13   
4         1  280201   4       1         1   5700       0       0      12   
5         1  120201   4       1         1   5200       0       0      12   
6         1  180101   3       1         1   4300       0       0      13   
7         1  140201   4       1         1    100       0       0      12   
8         1  140401   4       1         1    300       0       0      12   
9         1  280201   4       1         1   4100       0       0      12   

   RELATED  SEX  AGE  
0     1301    2   86  
1     1301    1   60  
2     1270    1   20  
3     1301    2   13  
4     1270    1   18  
5     1270    1   19  
6     1301    1   37  
7     1270    1   71  
8     1270    2   75  
9     1270    2   19

In [11]:
def get_momloc_head(row, df):
    head = df[(df['SERIAL'] == row['SERIAL']) & (df['RELATE'] == 1)]
    if not head.empty:
        return int(head.iloc[0]['MOMLOC'])
    return None

df['MOMLOC_HEAD'] = df.apply(lambda row: get_momloc_head(row, df_mass), axis=1)
df_mass = df[df['STATEICP'] == 3]
df_mass


KeyboardInterrupt: 

In [9]:
FLAG_TO_DIGITS = {'HU': '00',
                  'GQ': '01'}          
ser = result_data['SERIALNO'].astype(str)            
result_data['SERIALNO_NEW'] = (
    ser.str[:4]                                   
    + ser.str[4:6].map(FLAG_TO_DIGITS).fillna('99')   
    + ser.str[6:]                                 
).astype(np.int64)    
# ipums_res_merge = pd.concat([ipums_df, result_data])
# ipums_res_merge[['CBSERIAL_NEW']]
# ipums_df[['CBSERIAL_NEW']]
# for i in ipums_df['CBSERIAL'].unique():
#     print(i)
# result_data[['SERIALNO_NEW']]
# df_mass_res_merged = pd.concat([df_mass, result_data[['SERIALNO_NEW', 'MOM_LOC_HEAD']]], ignore_index=True)
df_mass_res_merged = pd.merge(df_mass,
                        result_data,
                        left_on=['CBSERIAL', 'PERNUM'],
                        right_on=['SERIALNO_NEW', 'SPORDER'],
                        how='inner')
df_mass_res_merged 

YEAR  SAMPLE  SERIAL       CBSERIAL   HHWT        CLUSTER  STATEICP  \
0      2023  202301  648436  2023010000077   1100  2023006484361         3   
1      2023  202301  648437  2023010000098   1100  2023006484371         3   
2      2023  202301  648438  2023010000109   8000  2023006484381         3   
3      2023  202301  648439  2023010000114   6900  2023006484391         3   
4      2023  202301  648440  2023010000135   2700  2023006484401         3   
...     ...     ...     ...            ...    ...            ...       ...   
73121  2023  202301  682484  2023001459883  14700  2023006824841         3   
73122  2023  202301  682484  2023001459883  14700  2023006824841         3   
73123  2023  202301  682484  2023001459883  14700  2023006824841         3   
73124  2023  202301  682485  2023001459891   9400  2023006824851         3   
73125  2023  202301  682486  2023001459906   4400  2023006824861         3   

       STATEFIP  STRATA  GQ  ...  WGTP73  WGTP74  WGTP75  WGTP76  WGTP77  \
0            25   50325   4  ...       0       0       0       0       0   
1            25   61325   4  ...       0       0       0       0       0   
2            25   61325   3  ...       0       0       0       0       0   
3            25   80125   4  ...       0       0       0       0       0   
4            25  120125   4  ...       0       0       0       0       0   
...         ...     ...  ..  ...     ...     ...     ...     ...     ...   
73121        25   50225   1  ...      44      41     257     264      46   
73122        25   50225   1  ...      44      41     257     264      46   
73123        25   50225   1  ...      44      41     257     264      46   
73124        25   80125   1  ...      31      93      22     136      95   
73125        25   80425   1  ...      17      54      10      10      70   

       WGTP78  WGTP79  WGTP80  MOM_LOC_HEAD   SERIALNO_NEW  
0           0       0       0          None  2023010000077  
1           0       0       0          None  2023010000098  
2           0       0       0          None  2023010000109  
3           0       0       0          None  2023010000114  
4           0       0       0          None  2023010000135  
...       ...     ...     ...           ...            ...  
73121     147     228     132          None  2023001459883  
73122     147     228     132          None  2023001459883  
73123     147     228     132          None  2023001459883  
73124      30      20      67          None  2023001459891  
73125      81      46      39          None  2023001459906  

[73126 rows x 549 columns]

In [10]:
for i, row in df_mass_res_merged[['MOMLOC_HEAD', 'MOM_LOC_HEAD']].iterrows():
    print(i, row)

0 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 0, dtype: object
1 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 1, dtype: object
2 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 2, dtype: object
3 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 3, dtype: object
4 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 4, dtype: object
5 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 5, dtype: object
6 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 6, dtype: object
7 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 7, dtype: object
8 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 8, dtype: object
9 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 9, dtype: object
10 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 10, dtype: object
11 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 11, dtype: object
12 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 12, dtype: object
13 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 13, dtype: object
14 MOMLOC_HEAD      NaN
MOM_LOC_HEAD    None
Name: 14,